In [10]:
%load_ext autoreload
%autoreload 2

import numpy as np
from strategy_v2.Strategy import *
from strategy_v2.Strategy.MVO import *
from strategy_v2.Strategy.MVO.AlphaModel import *
from strategy_v2.Strategy.MVO.RiskModel import *
from strategy_v2.TradingSubSystem import *
from strategy_v2.Portfolio import *
from strategy_v2.TransactionCost import *
from strategy_v2.Executor import *
from utils.data_helper import *
from utils.data import *
from utils.performance import *

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
instruments = [
    'META',
    'TSLA',
    'NVDA',
    'AAPL',
    'EWY',
    'DXJ',
    'BRK-B',
    'SPY',
    'QQQ'
]

end_date = get_today()
start_date = pd.to_datetime(datetime(2022, 1, 3))
max_leverage = 1
vol_target = 0.25

# Notes

- 2024-08-28: Tested expected return prediction with RandomForest, XGB, LGBM. None of them outperforms the SMA Model. LGBM is able to achieve a similar performance as SMA model and generally train faster.</br>

    | Measure                | ^SPX      | MVO - SMA1 | MVO - RandomForest1 | MVO - XGB1 | MVO - LGBM1 |
    |------------------------|-----------|------------|---------------------|------------|-------------|
    | Cumulative Return      | 1.173503  | 2.072994   | 1.662573            | 1.471717   | 2.023378    |
    | Annualized Return      | 0.076775  | 0.301537   | 0.221185            | 0.176047   | 0.296252    |
    | Annualized Volatility  | 0.180081  | 0.226417   | 0.240133            | 0.243953   | 0.243120    |
    | Annualized Sharpe Ratio| 0.240438  | 1.183923   | 0.781685            | 0.584416   | 1.080844    |
    | Maximum Drawdown       | -0.254251 | -0.271732  | -0.323658           | -0.380737  | -0.296535   |

    Models are shared the same hyperparameters: lookback (train days) = 10 days and gamma=10, hhi=0.2


In [12]:
portfolio = PortfolioStandard(
    capital=169336.48958837058,
    name='MVOPortfolio',        
    rebalance_iter=RebalancerIter('0 0 * * Fri', 2),        
    tc_model=TransactionCostFutu(), 
    systems=[        
        TradingSubSystemSingle(vol_target=vol_target, instruments=instruments, strategy=[MeanVarianceOpt(alpha_model=LGBM(5,10), risk_model=RollingMeanCov(10), gamma=10, hhi=0.2, confidence=1)], max_leverage=max_leverage, offset=60),
        TradingSubSystemSingle(vol_target=vol_target, instruments=instruments, strategy=[MeanVarianceOpt(alpha_model=RollingMean(10), risk_model=RollingMeanCov(10), gamma=10, hhi=0.2, confidence=1)], max_leverage=max_leverage, offset=60),        
    ]
)

portfolio.set_start_date(start_date)
portfolio.set_end_date(end_date)
portfolio.backtest_subsystems()
portfolio.optimize()
portfolio.backtest()
portfolio.rebalance()
portfolio.performance(show_all_rets=True)

[*********************100%***********************]  9 of 9 completed

2024-09-02 01:57:31,327 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Generating position for strategy MVO - LGBM1 between 2018-01-02 and 2024-09-01......


100%|██████████| 1739/1739 [02:48<00:00, 10.34it/s]
2024-09-02 02:00:19,522 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Volatility Target = 25.0% | Price Volatility = 27.7% | Last Scale Factor = 0.89
2024-09-02 02:00:19,524 - TradingSubSystemSingle [MVO - RollingMean1] - INFO - Generating position for strategy MVO - RollingMean1 between 2018-01-02 and 2024-09-01......
100%|██████████| 1739/1739 [00:10<00:00, 171.78it/s]
2024-09-02 02:00:29,665 - TradingSubSystemSingle [MVO - RollingMean1] - INFO - Volatility Target = 25.0% | Price Volatility = 25.2% | Last Scale Factor = 0.97


[*********************100%***********************]  1 of 1 completed


Rebalanced Portfolio  Optimized Portfolio      ^SPX   
Measure                                                                        
Cumulative Return                    5.806852             6.078986  2.081930  \
Annualized Return                    0.292732             0.299512  0.130386   
Annualized Volatility                0.237208             0.236609  0.200012   
Annualized Sharpe Ratio              1.092944             1.124365  0.484515   
Maximum Drawdown                    -0.297884            -0.329912 -0.339250   

                         MVO - LGBM1  MVO - RollingMean1  
Measure                                                   
Cumulative Return           6.339209            6.148749  
Annualized Return           0.305762            0.297856  
Annualized Volatility       0.236394            0.221849  
Annualized Sharpe Ratio     1.151828            1.191705  
Maximum Drawdown           -0.293224           -0.286799

In [4]:
portfolio.get_position_for_trade()

2024-08-27 02:12:11,586 - Standard Portfolio ({self.name}) - CRITICAL - Portfolio target capital is not specified, use initial backtest capital of $169,336
2024-08-27 02:12:11,587 - Standard Portfolio ({self.name}) - INFO - Generate trade position based on target capital of $169,336


Empty DataFrame
Columns: []
Index: []

# Execute the Portfolio

In [168]:
# executor = ExecutorFutu(is_test=True)
# executor.set_portfolio(portfolio)
# orders = executor.execute(px_interval='5m')
# orders

# Calibration Portfolios

In [43]:
import itertools

def calbiration(start_date, end_date, params):
    sumamry = []

    for p in params:
        portfolio = PortfolioStandard(
            capital=169336.48958837058,
            name='MVOPortfolio',        
            rebalance_iter=RebalancerIter('0 0 * * Fri', 2),        
            tc_model=TransactionCostFutu(), 
            systems=[                                        
                TradingSubSystemSingle(vol_target=vol_target, instruments=instruments,  strategy=[MeanVarianceOptLGBM(gamma=10, hhi=0.2, lookback=10, confidence=1, train_days=p[0], forecast=p[1])], max_leverage=max_leverage, offset=60),                
            ]
        )
        portfolio.set_start_date(start_date)
        portfolio.set_end_date(end_date)
        portfolio.backtest_subsystems()

        ret = (portfolio.ret).mean(axis=1)
        res = performance_summary(ret)
        del res['strategy']
        res['train_days'] = p[0]
        res['forecast'] = p[1]
        sumamry.append(res)

    summary = pd.DataFrame(sumamry)
    summary = summary.set_index(['train_days', 'forecast'])    
    return summary

start_date = pd.to_datetime(datetime(2023,1,1))
end_date = get_today()

forcasts = np.arange(1,20,2)
train_days = forcasts * 3
params = list(itertools.product(train_days, forcasts))
params = [[p[0], p[1]] for p in params if p[0] > p[1]]

summary = calbiration(start_date, end_date, params)

2024-08-28 02:41:01,504 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Generating position for strategy MVO - LGBM1 between 2022-12-30 and 2024-08-27......
100%|██████████| 433/433 [00:41<00:00, 10.49it/s]
2024-08-28 02:41:42,847 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Volatility Target = 25.0% | Price Volatility = 34.7% | Last Scale Factor = 0.71
2024-08-28 02:41:42,852 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Generating position for strategy MVO - LGBM1 between 2022-12-30 and 2024-08-27......
100%|██████████| 433/433 [00:44<00:00,  9.78it/s]
2024-08-28 02:42:27,176 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Volatility Target = 25.0% | Price Volatility = 30.1% | Last Scale Factor = 0.83
2024-08-28 02:42:27,183 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Generating position for strategy MVO - LGBM1 between 2022-12-30 and 2024-08-27......
100%|██████████| 433/433 [00:42<00:00, 10.30it/s]
2024-08-28 02:43:09,268 - TradingSubSystemSingle [MVO - LGBM1] - INFO - Vol